In [4]:
import Pkg
Pkg.activate(".")
Pkg.instantiate()

using Plots, QuadGK, Dierckx, SpecialFunctions, LaTeXStrings

###analytical results 
#multiplicative 
sigma = 0.3
U(x) = (k1*x^4)/4 - (k2*x^3)/3 + (k3*x^2)/2 - k4*x
k1 = 0.02;k2 = 0.20;k3 = 0.55;k4 = 0.4
f(x) = -k1*x^3+(k2*x^2)-k3*x+k4
g(x) = sigma*sqrt(k1*x^3 + k2*x^2 + k3*x + k4)

  Activating project at `~/Desktop/tpt_code`


g (generic function with 1 method)

In [13]:
function export_reactive_density(sigma)
    g(x) = sigma
    x_grid = range(0,12,10^5);#grid for stationary distribution
    left_min = 2.5; right_min = 5;
    q_range = range(left_min, right_min, 10^5)##grid for tpt
    exp_int = zeros(100000) # ∫-U'[x]/g^2[x]
    Ps_grid = zeros(100000) # stationary distribution
    for i in 2:100000
        exp_int[i] = quadgk(x -> f(x)/g(x)^2, 0, x_grid[i], rtol=1e-5)[1]
        Ps_grid[i] = 1/g(x_grid[i])^2*exp(2*exp_int[i])
    end
    spl_Ps = Spline1D(x_grid, Ps_grid)
    Nps = integrate(spl_Ps, 0,12)#normalization constant 
    exp_int_dq = zeros(100000) #∫U'[x]/g^2[x]
    dq_grid = zeros(100000) #dq = q'[x]
    for i in 2:100000
        exp_int_dq[i] = quadgk(x -> -f(x)/g(x)^2, 0, q_range[i], rtol=1e-5)[1]
        dq_grid[i] = exp(2*exp_int_dq[i])
    end
    #plot(q_range[2:end], dq_grid[2:end])#plot dq
    spl = Spline1D(q_range[2:end], dq_grid[2:end])
    Nq = integrate(spl, left_min, right_min) #normalization constant 
    q_grid = zeros(100000) # q_plus
    for i in 2:100000
        q_grid[i] = integrate(spl, left_min, q_range[i])
        q_grid[i]  = q_grid[i]/Nq
    end
    #plot(q_range, q_grid) # plot q_plus
    muAB_grid = zeros(100000)
    for i in 1:100000
        muAB_grid[i] = spl_Ps(q_range[i])/Nps * q_grid[i] * (1 - q_grid[i])
    end
    spl = Spline1D(q_range, muAB_grid)
    NmuAB = integrate(spl, left_min, right_min)#normalization constant 
    return q_range, muAB_grid./NmuAB
end

q_range, muAB_grid1 = export_reactive_density(0.3)
q_range, muAB_grid2 = export_reactive_density(0.45)
q_range, muAB_grid3 = export_reactive_density(0.6)


(2.5:2.5000250002500026e-5:5.0, [0.0, 0.0, 2.7169854050734095e-5, 5.4338864549220985e-5, 8.150703150986715e-5, 0.00010867435494756189, 0.00013584083487671193, 0.00016300647131317205, 0.00019017126427134932, 0.00021733521376565086  …  0.0002445004908008644, 0.0002173369292489941, 0.00019017257778998083, 0.000163007436422588, 0.0001358415051433843, 0.00010867478395113636, 8.1507272843148e-5, 5.433897181672484e-5, 2.7169880869905995e-5, 0.0])

In [15]:
p1 = plot(q_range, muAB_grid1, label = L"\sigma = 0.30");
plot!(q_range, muAB_grid2, label = L"\sigma = 0.45", xlab = L"x",ylab = L"\rho_{AB}(x)" ,legend =:topright,foreground_color_legend = nothing, grid = false, title = "Additive noise")
plot!(q_range, muAB_grid3, label = L"\sigma = 0.60", xlab = L"x",ylab = L"\rho_{AB}(x)" ,legend =:topright,foreground_color_legend = nothing, grid = false, title = "Additive noise", labelsize = 1.5,  ytickfont=font(15), xtickfont=font(15), guidefont=font(25), legendfont = font(14), size = (600,400), framestyle = :box)
savefig("figure/Schlogl_model_add.pdf")
p1

In [10]:
function export_reactive_density_mul(sigma)
    g(x) = sigma*sqrt(k1*x^3 + k2*x^2 + k3*x + k4)
    x_grid = range(0,12,10^5);#grid for stationary distribution
    left_min = 2.5; right_min = 5;
    q_range = range(left_min, right_min, 10^5)##grid for tpt
    exp_int = zeros(100000) # ∫-U'[x]/g^2[x]
    Ps_grid = zeros(100000) # stationary distribution
    for i in 2:100000
        exp_int[i] = quadgk(x -> f(x)/g(x)^2, 0, x_grid[i], rtol=1e-5)[1]
        Ps_grid[i] = 1/g(x_grid[i])^2*exp(2*exp_int[i])
    end
    spl_Ps = Spline1D(x_grid, Ps_grid)
    Nps = integrate(spl_Ps, 0,12)#normalization constant 
    exp_int_dq = zeros(100000) #∫U'[x]/g^2[x]
    dq_grid = zeros(100000) #dq = q'[x]
    for i in 2:100000
        exp_int_dq[i] = quadgk(x -> -f(x)/g(x)^2, 0, q_range[i], rtol=1e-5)[1]
        dq_grid[i] = exp(2*exp_int_dq[i])
    end
    #plot(q_range[2:end], dq_grid[2:end])#plot dq
    spl = Spline1D(q_range[2:end], dq_grid[2:end])
    Nq = integrate(spl, left_min, right_min) #normalization constant 
    q_grid = zeros(100000) # q_plus
    for i in 2:100000
        q_grid[i] = integrate(spl, left_min, q_range[i])
        q_grid[i]  = q_grid[i]/Nq
    end
    #plot(q_range, q_grid) # plot q_plus
    muAB_grid = zeros(100000)
    for i in 1:100000
        muAB_grid[i] = spl_Ps(q_range[i])/Nps * q_grid[i] * (1 - q_grid[i])
    end
    spl = Spline1D(q_range, muAB_grid)
    NmuAB = integrate(spl, left_min, right_min)#normalization constant 
    return q_range, muAB_grid./NmuAB
end

q_range, muAB_grid1 = export_reactive_density_mul(0.1)
q_range, muAB_grid2 = export_reactive_density_mul(0.3)
q_range, muAB_grid3 = export_reactive_density_mul(0.45)
p2 = plot(q_range, muAB_grid1, label = L"\sigma = 0.30");
plot!(q_range, muAB_grid2, label = L"\sigma = 0.45", xlab = L"x",ylab = L"\rho_{AB}(x)" ,legend =:topright,foreground_color_legend = nothing, grid = false, title = "Multiplicative noise")
plot!(q_range, muAB_grid3, label = L"\sigma = 0.60", xlab = L"x",ylab = L"\rho_{AB}(x)" ,legend =:topright,foreground_color_legend = nothing, grid = false, title = "Multiplicative noise", labelsize = 1.5,  ytickfont=font(15), xtickfont=font(15), guidefont=font(25), legendfont = font(14), size = (600,400), framestyle = :box)
savefig("figure/Schlogl_model_mul.pdf")
p2